# League of Legends Predictor

**Name(s)**: Jawad Najar and Ali Boussi

**Website Link**: (your website link)

In [115]:
import pandas as pd
import numpy as np

import plotly.express as px
pd.options.plotting.backend = 'plotly'
pd.set_option('display.max_columns', None)

## Step 1: Introduction

###

In [116]:
raw_data = pd.read_csv('data.csv')
raw_data.head()

/var/folders/0x/vxx84z8n5nx30fmvgrp26j1r0000gn/T/ipykernel_61258/3741442452.py:1: DtypeWarning:

Columns (2) have mixed types. Specify dtype option on import or set low_memory=False.



gameid datacompleteness  url league  year   split  playoffs  \
0  ESPORTSTMNT01_2690210         complete  NaN   LCKC  2022  Spring         0   
1  ESPORTSTMNT01_2690210         complete  NaN   LCKC  2022  Spring         0   
2  ESPORTSTMNT01_2690210         complete  NaN   LCKC  2022  Spring         0   
3  ESPORTSTMNT01_2690210         complete  NaN   LCKC  2022  Spring         0   
4  ESPORTSTMNT01_2690210         complete  NaN   LCKC  2022  Spring         0   

                  date  game  patch  participantid  side position playername  \
0  2022-01-10 07:44:08     1  12.01              1  Blue      top     Soboro   
1  2022-01-10 07:44:08     1  12.01              2  Blue      jng     Raptor   
2  2022-01-10 07:44:08     1  12.01              3  Blue      mid     Feisty   
3  2022-01-10 07:44:08     1  12.01              4  Blue      bot      Gamin   
4  2022-01-10 07:44:08     1  12.01              5  Blue      sup      Loopy   

                                    playerid           teamname  \
0  oe:player:38e0af7278d6769d0c81d7c4b47ac1e  BRION Challengers   
1  oe:player:637ed20b1e41be1c51bd1a4cb211357  BRION Challengers   
2  oe:player:d1ae0e2f9f3ac1e0e0cdcb86504ca77  BRION Challengers   
3  oe:player:998b3e49b01ecc41eacc392477a98cf  BRION Challengers   
4  oe:player:e9741b3a238723ea6380ef2113fae63  BRION Challengers   

                                    teamid  champion   ban1     ban2    ban3  \
0  oe:team:733ebb9dbf22a401c0127a0c80193ca  Renekton  Karma  Caitlyn  Syndra   
1  oe:team:733ebb9dbf22a401c0127a0c80193ca  Xin Zhao  Karma  Caitlyn  Syndra   
2  oe:team:733ebb9dbf22a401c0127a0c80193ca   LeBlanc  Karma  Caitlyn  Syndra   
3  oe:team:733ebb9dbf22a401c0127a0c80193ca    Samira  Karma  Caitlyn  Syndra   
4  oe:team:733ebb9dbf22a401c0127a0c80193ca     Leona  Karma  Caitlyn  Syndra   

     ban4  ban5 pick1 pick2 pick3 pick4 pick5  gamelength  result  kills  \
0  Thresh  Lulu   NaN   NaN   NaN   NaN   NaN        1713       0      2   
1  Thresh  Lulu   NaN   NaN   NaN   NaN   NaN        1713       0      2   
2  Thresh  Lulu   NaN   NaN   NaN   NaN   NaN        1713       0      2   
3  Thresh  Lulu   NaN   NaN   NaN   NaN   NaN        1713       0      2   
4  Thresh  Lulu   NaN   NaN   NaN   NaN   NaN        1713       0      1   

   deaths  assists  teamkills  teamdeaths  doublekills  triplekills  \
0       3        2          9          19          0.0          0.0   
1       5        6          9          19          0.0          0.0   
2       2        3          9          19          0.0          0.0   
3       4        2          9          19          0.0          0.0   
4       5        6          9          19          0.0          0.0   

   quadrakills  pentakills  firstblood  firstbloodkill  firstbloodassist  \
0          0.0         0.0         0.0             0.0               0.0   
1          0.0         0.0         1.0             0.0               1.0   
2          0.0         0.0         0.0             0.0               0.0   
3          0.0         0.0         1.0             0.0               1.0   
4          0.0         0.0         1.0             1.0               0.0   

   firstbloodvictim  team kpm    ckpm  firstdragon  dragons  opp_dragons  \
0               0.0    0.3152  0.9807          NaN      NaN          NaN   
1               0.0    0.3152  0.9807          NaN      NaN          NaN   
2               0.0    0.3152  0.9807          NaN      NaN          NaN   
3               0.0    0.3152  0.9807          NaN      NaN          NaN   
4               0.0    0.3152  0.9807          NaN      NaN          NaN   

   elementaldrakes  opp_elementaldrakes  infernals  mountains  clouds  oceans  \
0              NaN                  NaN        NaN        NaN     NaN     NaN   
1              NaN                  NaN        NaN        NaN     NaN     NaN   
2              NaN                  NaN        NaN        NaN     NaN     NaN   
3              NaN                  NaN     

## Step 2: Data Cleaning and Exploratory Data Analysis

#### Data Cleaning

In [130]:
df = raw_data.copy()

# filter for complete data
df = df[df['datacompleteness'] == 'complete']

# drop unnecessary columns (metadata
meta_columns = ['participantid', 'playerid', 'teamid', 
                'datacompleteness', 'url', 'league', 
                'year', 'split', 'playoffs','date', 'game',
                'teamname', 'playername', 'patch']
df = df.drop(columns=meta_columns)

# seperate team and player stats
team_df = df[df['position'] == 'team']
player_df = df[df['position'] != 'team']

# Dropping all columnsn that are all NaN (it is a tea/player stat, respectively)
player_df = player_df.dropna(axis=1, how='all')
team_df = team_df.dropna(axis=1, how='all')

# Team Adv columns 
team_df['tower_advantage'] = team_df['towers'] - team_df['opp_towers']
team_df['inhibitor_advantage'] = team_df['inhibitors'] - team_df['opp_inhibitors']

In [131]:
fig = px.histogram(
    team_df,
    x='tower_advantage',
    nbins=15,  
    title='Distribution of Tower Advantage',
    labels={'tower_advantage': 'Tower Advantage (Team - Opponent)'},
    color_discrete_sequence=['indianred'] 
)

fig.update_layout(
    bargap=0.1, 
    template='plotly_white',  
    xaxis_title='Tower Advantage',
    yaxis_title='Number of Games',
    font=dict(size=14)
)

fig.show()

In [132]:
fig = px.histogram(
    team_df,
    x='inhibitor_advantage',
    nbins=15, 
    title='Distribution of Inhibitor Advantage',
    labels={'inhibitor_advantage': 'Inhibitor Advantage (Team - Opponent)'},
    color_discrete_sequence=['skyblue'] 
)

fig.update_layout(
    bargap=0.1, 
    template='plotly_white', 
    xaxis_title='Inhibitor Advantage',
    yaxis_title='Number of Games',
    font=dict(size=14)
)

fig.show()

In [120]:
# Creating a copy df
gold_stats = team_df.copy()[['gameid', 'earnedgold', 'side', 'result']]

gold_stats['red_win'] = ((gold_stats['result'] == 1) & ((gold_stats['side'] == 'Red')))
red_side_gold = gold_stats.loc[gold_stats['side'] == 'Red', ['gameid', 'earnedgold', 'red_win']]
blue_side_gold =  gold_stats.loc[gold_stats['side'] == 'Blue', ['gameid', 'earnedgold']]
gold_final = red_side_gold.merge(blue_side_gold, on='gameid', suffixes=('_red', '_blue'))

fig = px.scatter(
    gold_final,
    x='earnedgold_red',
    y='earnedgold_blue',
    color='red_win',
    color_discrete_map={True: '#D2042D', False: '#0047AB'},
    opacity=0.6,
    hover_data={
        'earnedgold_red': ':.0f',
        'earnedgold_blue': ':.0f',
        'red_win': True
    },
    labels={
        'earnedgold_red': 'Red Team Gold',
        'earnedgold_blue': 'Blue Team Gold',
        'red_win': 'Red Team Won'
    },
    title='Red Gold Earned vs Blue Gold Earned by Game Outcome'
)

fig.update_traces(marker=dict(size=6))

fig.update_layout(
    width=900,
    height=600,
    title_font_size=20,
    xaxis=dict(title='Red Team Earned Gold', tickformat=',', title_font_size=16),
    yaxis=dict(title='Blue Team Earned Gold', tickformat=',', title_font_size=16),
    legend_title_text='Red Team Win?',
    legend=dict(font=dict(size=12))
)

fig.show()

In [ ]:
fig = px.scatter(
    player_df,
    x='goldat10',
    y='opp_goldat10',
    color='position'
)
fig.show()
# player_df.columns[player_df.columns.str.contains('gold')]

# look at a winning game -- not showing duplicate data
# make a feature -- gold difference per position (data cleaning)
# for every position, take the players gold at a time minus their oppgold at that time
# plot position on x and gold diff on y?



In [150]:
df_numeric = team_df.select_dtypes(include=['number'])
correlations = df_numeric.corr()['result'].abs().sort_values(ascending=False)

correlations.head(20)
player_df.head()


gameid  side position  champion   ban1     ban2    ban3  \
0  ESPORTSTMNT01_2690210  Blue      top  Renekton  Karma  Caitlyn  Syndra   
1  ESPORTSTMNT01_2690210  Blue      jng  Xin Zhao  Karma  Caitlyn  Syndra   
2  ESPORTSTMNT01_2690210  Blue      mid   LeBlanc  Karma  Caitlyn  Syndra   
3  ESPORTSTMNT01_2690210  Blue      bot    Samira  Karma  Caitlyn  Syndra   
4  ESPORTSTMNT01_2690210  Blue      sup     Leona  Karma  Caitlyn  Syndra   

     ban4  ban5  gamelength  result  kills  deaths  assists  teamkills  \
0  Thresh  Lulu        1713       0      2       3        2          9   
1  Thresh  Lulu        1713       0      2       5        6          9   
2  Thresh  Lulu        1713       0      2       2        3          9   
3  Thresh  Lulu        1713       0      2       4        2          9   
4  Thresh  Lulu        1713       0      1       5        6          9   

   teamdeaths  doublekills  triplekills  quadrakills  pentakills  firstblood  \
0          19          0.0          0.0          0.0         0.0         0.0   
1          19          0.0          0.0          0.0         0.0         1.0   
2          19          0.0          0.0          0.0         0.0         0.0   
3          19          0.0          0.0          0.0         0.0         1.0   
4          19          0.0          0.0          0.0         0.0         1.0   

   firstbloodkill  firstbloodassist  firstbloodvictim  team kpm    ckpm  \
0             0.0               0.0               0.0    0.3152  0.9807   
1             0.0               1.0               0.0    0.3152  0.9807   
2             0.0               0.0               0.0    0.3152  0.9807   
3             0.0               1.0               0.0    0.3152  0.9807   
4             1.0               0.0               0.0    0.3152  0.9807   

   barons  opp_barons  inhibitors  opp_inhibitors  damagetochampions  \
0     0.0         0.0         0.0             0.0            15768.0   
1     0.0         0.0         0.0             1.0            11765.0   
2     0.0         0.0         0.0             0.0            14258.0   
3     0.0         0.0         0.0             0.0            11106.0   
4     0.0         0.0         0.0             0.0             3663.0   

        dpm  damageshare  damagetakenperminute  damagemitigatedperminute  \
0  552.2942     0.278784             1072.3993                  777.7933   
1  412.0841     0.208009              944.2732                  650.1576   
2  499.4046     0.252086              581.6462                  227.7758   
3  389.0018     0.196358              463.8529                  218.8792   
4  128.3012     0.064763              475.0263                  490.1226   

   wardsplaced     wpm  wardskilled    wcpm  controlwardsbought  visionscore  \
0          8.0  0.2802          6.0  0.2102                 5.0         26.0   
1          6.0  0.2102         18.0  0.6305                 6.0         48.0   
2         19.0  0.6655          7.0  0.2452                 7.0         29.0   
3         12.0  0.4203          6.0  0.2102                 4.0         25.0   
4         29.0  1.0158         14.0  0.4904                11.0         69.0   

     vspm  totalgold  earnedgold  earned gpm  earnedgoldshare  goldspent  \
0  0.9107      10934      7164.0    250.9282         0.253859    10275.0   
1  1.6813       9138      5368.0    188.0210         0.190220     8750.0   
2  1.0158       9715      5945.0    208.2312         0.210665     8725.0   
3  0.8757      10605      6835.0    239.4046         0.242201    10425.0   
4  2.4168       6678      2908.0    101.8564         0.103054     6395.0   

   total cs  minionkills  monsterkills  monsterkillsownjungle  \
0     231.0        220.0          11.0                    NaN   
1     148.0         33.0         115.0                    NaN   
2     193.0        177.0          16.0                    NaN   
3     226.0        208.0          18.0                    NaN   
4      42.0         42.0 

## Step 3: Framing a Prediction Problem

In [ ]:
# TODO

## Step 4: Baseline Model

In [ ]:
# TODO

## Step 5: Final Model

In [ ]:
# TODO